In [0]:
import urllib
import math
from sklearn.metrics import accuracy_score
from pyspark.ml.feature import Tokenizer, StopWordsRemover
from pyspark.sql.functions import col, lower, regexp_replace, length, trim, size
from pyspark.sql.types import StringType, ArrayType


In [0]:

dataUrl = 'https://archive.org/download/spam-text-mesg-dataset/SPAM_Text_Mesg_Dataset.csv'
temp_file_path = "/SPAM_Text_Mesg_Dataset.csv"
urllib.request.urlretrieve(dataUrl, temp_file_path)
dbutils.fs.mv(f"file:{temp_file_path}", f"dbfs:{temp_file_path}")


Out[191]: True

In [0]:
display(dataset)


Category Message real Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat... real Ok lar... Joking wif u oni... spam Free entry in 2 a wkly comp to win FA Cup final tkts 21st May 2005. Text FA to 87121 to receive entry question(std txt rate)T&C's apply 08452810075over18's real U dun say so early hor... U c already then say... real Nah I don't think he goes to usf, he lives around here though spam FreeMsg Hey there darling it's been 3 week's now and no word back! I'd like some fun you up for it still? Tb ok! XxX std chgs to send, £1.50 to rcv real Even my brother is not like to speak with me. They treat me like aids patent. real As per your request 'Melle Melle (Oru Minnaminunginte Nurungu Vettam)' has been set as your callertune for all Callers. Press *9 to copy your friends Callertune spam WINNER!! As a valued network customer you have been selected to receivea £900 prize reward! To claim call 09061701461. Claim code KL341. Valid 12 hours only. spam Had your mobile 11 months or more? U R entitled to Update to the latest colour mobiles with camera for Free! Call The Mobile Update Co FREE on 08002986030 real I'm gonna be home soon and i don't want to talk about this stuff anymore tonight, k? I've cried enough today. spam SIX chances to win CASH! From 100 to 20,000 pounds txt> CSH11 and send to 87575. Cost 150p/day, 6days, 16+ TsandCs apply Reply HL 4 info spam URGENT! You have won a 1 week FREE membership in our £100,000 Prize Jackpot! Txt the word: CLAIM to No: 81010 T&C www.dbuk.net LCCLTD POBOX 4403LDNW1A7RW18 real I've been searching for the right words to thank you for this breather. I promise i wont take your help for granted and will fulfil my promise. You have been wonderful and a blessing at all times. real I HAVE A DATE ON SUNDAY WITH WILL!! spam XXXMobileMovieClub: To use your credit, click the WAP link in the next txt message or click here>> http://wap. xxxmobilemovieclub.com?n=QJKGIGHJJGCBL real Oh k...i'm watching here:) real Eh u remember how 2 spell his name... Yes i did. He v naughty make until i v wet. real Fine if thats the way u feel. Thats the way its gota b spam England v Macedonia - dont miss the goals/team news. Txt ur national team to 87077 eg ENGLAND to 87077 Try:WALES, SCOTLAND 4txt/ú1.20 POBOXox36504W45WQ 16+ real Is that seriously how you spell his name? real I‘m going to try for 2 months ha ha only joking real So ü pay first lar... Then when is da stock comin... real Aft i finish my lunch then i go str down lor. Ard 3 smth lor. U finish ur lunch already? real Ffffffffff. Alright no way I can meet up with you sooner? real Just forced myself to eat a slice. I'm really not hungry tho. This sucks. Mark is getting worried. He knows I'm sick when I turn down pizza. Lol real Lol your always so convincing. real Did you catch the bus ? Are you frying an egg ? Did you make a tea? Are you eating your mom's left over dinner ? Do you feel my Love ? real I'm back & we're packing the car now, I'll let you know if there's room real Ahhh. Work. I vaguely remember that! What does it feel like? Lol real Wait that's still not all that clear, were you not sure about me being sarcastic or that that's why x doesn't want to live with us real Yeah he got in at 2 and was v apologetic. n had fallen out and she was actin like spoilt child and he got caught up in that. Till 2! But we won't go there! Not doing too badly cheers. You? real K tell me anything about you. real For fear of fainting with the of all that housework you just did? Quick have a cuppa spam Thanks for your subscription to Ringtone UK your mobile will be charged £5/month Please confirm by replying YES or NO. If you reply NO you will not be charged real Yup... Ok i go home look at the timings then i msg ü again... Xuhui going to learn on 2nd may too but her lesson is at 8am real Oops, I'll let you know when my roommate's done real I see the letter B on my car real Anything lor... U decide... real Hello

In [0]:
# removing null data 
dataset = dataset.filter("Category is NOT NULL and Message is NOT NULL")
display(dataset)

Category Message real Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat... real Ok lar... Joking wif u oni... spam Free entry in 2 a wkly comp to win FA Cup final tkts 21st May 2005. Text FA to 87121 to receive entry question(std txt rate)T&C's apply 08452810075over18's real U dun say so early hor... U c already then say... real Nah I don't think he goes to usf, he lives around here though spam FreeMsg Hey there darling it's been 3 week's now and no word back! I'd like some fun you up for it still? Tb ok! XxX std chgs to send, £1.50 to rcv real Even my brother is not like to speak with me. They treat me like aids patent. real As per your request 'Melle Melle (Oru Minnaminunginte Nurungu Vettam)' has been set as your callertune for all Callers. Press *9 to copy your friends Callertune spam WINNER!! As a valued network customer you have been selected to receivea £900 prize reward! To claim call 09061701461. Claim code KL341. Valid 12 hours only. spam Had your mobile 11 months or more? U R entitled to Update to the latest colour mobiles with camera for Free! Call The Mobile Update Co FREE on 08002986030 real I'm gonna be home soon and i don't want to talk about this stuff anymore tonight, k? I've cried enough today. spam SIX chances to win CASH! From 100 to 20,000 pounds txt> CSH11 and send to 87575. Cost 150p/day, 6days, 16+ TsandCs apply Reply HL 4 info spam URGENT! You have won a 1 week FREE membership in our £100,000 Prize Jackpot! Txt the word: CLAIM to No: 81010 T&C www.dbuk.net LCCLTD POBOX 4403LDNW1A7RW18 real I've been searching for the right words to thank you for this breather. I promise i wont take your help for granted and will fulfil my promise. You have been wonderful and a blessing at all times. real I HAVE A DATE ON SUNDAY WITH WILL!! spam XXXMobileMovieClub: To use your credit, click the WAP link in the next txt message or click here>> http://wap. xxxmobilemovieclub.com?n=QJKGIGHJJGCBL real Oh k...i'm watching here:) real Eh u remember how 2 spell his name... Yes i did. He v naughty make until i v wet. real Fine if thats the way u feel. Thats the way its gota b spam England v Macedonia - dont miss the goals/team news. Txt ur national team to 87077 eg ENGLAND to 87077 Try:WALES, SCOTLAND 4txt/ú1.20 POBOXox36504W45WQ 16+ real Is that seriously how you spell his name? real I‘m going to try for 2 months ha ha only joking real So ü pay first lar... Then when is da stock comin... real Aft i finish my lunch then i go str down lor. Ard 3 smth lor. U finish ur lunch already? real Ffffffffff. Alright no way I can meet up with you sooner? real Just forced myself to eat a slice. I'm really not hungry tho. This sucks. Mark is getting worried. He knows I'm sick when I turn down pizza. Lol real Lol your always so convincing. real Did you catch the bus ? Are you frying an egg ? Did you make a tea? Are you eating your mom's left over dinner ? Do you feel my Love ? real I'm back & we're packing the car now, I'll let you know if there's room real Ahhh. Work. I vaguely remember that! What does it feel like? Lol real Wait that's still not all that clear, were you not sure about me being sarcastic or that that's why x doesn't want to live with us real Yeah he got in at 2 and was v apologetic. n had fallen out and she was actin like spoilt child and he got caught up in that. Till 2! But we won't go there! Not doing too badly cheers. You? real K tell me anything about you. real For fear of fainting with the of all that housework you just did? Quick have a cuppa spam Thanks for your subscription to Ringtone UK your mobile will be charged £5/month Please confirm by replying YES or NO. If you reply NO you will not be charged real Yup... Ok i go home look at the timings then i msg ü again... Xuhui going to learn on 2nd may too but her lesson is at 8am real Oops, I'll let you know when my roommate's done real I see the letter B on my car real Anything lor... U decide... real Hello

In [0]:
# pre-processing 

#removing punctuation
cleanText = dataset.select('Category' , (lower(regexp_replace('Message', "[\[\]#./\"'_—=`<>@&!-:;|?*“”\t’‘]", "")).alias('Message')))
display(cleanText)


Category Message real go until jurong point crazy available only in bugis n great world la e buffet cine there got amore wat real ok lar joking wif u oni spam free entry in a wkly comp to win fa cup final tkts st may text fa to to receive entry questionstd txt ratetcs apply overs real u dun say so early hor u c already then say real nah i dont think he goes to usf he lives around here though spam freemsg hey there darling its been weeks now and no word back id like some fun you up for it still tb ok xxx std chgs to send £ to rcv real even my brother is not like to speak with me they treat me like aids patent real as per your request melle melle oru minnaminunginte nurungu vettam has been set as your callertune for all callers press to copy your friends callertune spam winner as a valued network customer you have been selected to receivea £ prize reward to claim call claim code kl valid hours only spam had your mobile months or more u r entitled to update to the latest colour mobiles with camera for free call the mobile update co free on real im gonna be home soon and i dont want to talk about this stuff anymore tonight k ive cried enough today spam six chances to win cash from to pounds txt csh and send to cost pday days tsandcs apply reply hl info spam urgent you have won a week free membership in our £ prize jackpot txt the word claim to no tc wwwdbuknet lccltd pobox ldnwarw real ive been searching for the right words to thank you for this breather i promise i wont take your help for granted and will fulfil my promise you have been wonderful and a blessing at all times real i have a date on sunday with will spam xxxmobilemovieclub to use your credit click the wap link in the next txt message or click here httpwap xxxmobilemovieclubcomnqjkgighjjgcbl real oh kim watching here real eh u remember how spell his name yes i did he v naughty make until i v wet real fine if thats the way u feel thats the way its gota b spam england v macedonia dont miss the goalsteam news txt ur national team to eg england to trywales scotland txtú poboxoxwwq real is that seriously how you spell his name real im going to try for months ha ha only joking real so ü pay first lar then when is da stock comin real aft i finish my lunch then i go str down lor ard smth lor u finish ur lunch already real ffffffffff alright no way i can meet up with you sooner real just forced myself to eat a slice im really not hungry tho this sucks mark is getting worried he knows im sick when i turn down pizza lol real lol your always so convincing real did you catch the bus are you frying an egg did you make a tea are you eating your moms left over dinner do you feel my love real im back amp were packing the car now ill let you know if theres room real ahhh work i vaguely remember that what does it feel like lol real wait thats still not all that clear were you not sure about me being sarcastic or that thats why x doesnt want to live with us real yeah he got in at and was v apologetic n had fallen out and she was actin like spoilt child and he got caught up in that till but we wont go there not doing too badly cheers you real k tell me anything about you real for fear of fainting with the of all that housework you just did quick have a cuppa spam thanks for your subscription to ringtone uk your mobile will be charged £month please confirm by replying yes or no if you reply no you will not be charged real yup ok i go home look at the timings then i msg ü again xuhui going to learn on nd may too but her lesson is at am real oops ill let you know when my roommates done real i see the letter b on my car real anything lor u decide real hello hows you and how did saturday go i was just texting to see if youd decided to do anything tomo not that im trying to invite myself or anything real pls go ahead with watts i just wanted to be sure do have a great weekend abiola real did i forget to tell you i want you i need you i crave you but most of all i love you my sweet arabian ste

In [0]:
#tokenizing 
tokenizer = Tokenizer(inputCol='Message' , outputCol='MessageToken')
descTokenDF = tokenizer.transform(cleanText).select('Category' , 'MessageToken')
display(descTokenDF)

Category MessageToken real List(go, until, jurong, point, crazy, available, only, in, bugis, n, great, world, la, e, buffet, cine, there, got, amore, wat) real List(ok, lar, joking, wif, u, oni) spam List(free, entry, in, , a, wkly, comp, to, win, fa, cup, final, tkts, st, may, , text, fa, to, , to, receive, entry, questionstd, txt, ratetcs, apply, overs) real List(u, dun, say, so, early, hor, u, c, already, then, say) real List(nah, i, dont, think, he, goes, to, usf, he, lives, around, here, though) spam List(freemsg, hey, there, darling, its, been, , weeks, now, and, no, word, back, id, like, some, fun, you, up, for, it, still, tb, ok, xxx, std, chgs, to, send, £, to, rcv) real List(even, my, brother, is, not, like, to, speak, with, me, they, treat, me, like, aids, patent) real List(as, per, your, request, melle, melle, oru, minnaminunginte, nurungu, vettam, has, been, set, as, your, callertune, for, all, callers, press, , to, copy, your, friends, callertune) spam List(winner, as, a, valued, network, customer, you, have, been, selected, to, receivea, £, prize, reward, to, claim, call, , claim, code, kl, valid, , hours, only) spam List(had, your, mobile, , months, or, more, u, r, entitled, to, update, to, the, latest, colour, mobiles, with, camera, for, free, call, the, mobile, update, co, free, on) real List(im, gonna, be, home, soon, and, i, dont, want, to, talk, about, this, stuff, anymore, tonight, k, ive, cried, enough, today) spam List(six, chances, to, win, cash, from, , to, , pounds, txt, csh, and, send, to, , cost, pday, days, , tsandcs, apply, reply, hl, , info) spam List(urgent, you, have, won, a, , week, free, membership, in, our, £, prize, jackpot, txt, the, word, claim, to, no, , tc, wwwdbuknet, lccltd, pobox, ldnwarw) real List(ive, been, searching, for, the, right, words, to, thank, you, for, this, breather, i, promise, i, wont, take, your, help, for, granted, and, will, fulfil, my, promise, you, have, been, wonderful, and, a, blessing, at, all, times) real List(i, have, a, date, on, sunday, with, will) spam List(xxxmobilemovieclub, to, use, your, credit, click, the, wap, link, in, the, next, txt, message, or, click, here, httpwap, xxxmobilemovieclubcomnqjkgighjjgcbl) real List(oh, kim, watching, here) real List(eh, u, remember, how, , spell, his, name, yes, i, did, he, v, naughty, make, until, i, v, wet) real List(fine, if, thats, the, way, u, feel, thats, the, way, its, gota, b) spam List(england, v, macedonia, , dont, miss, the, goalsteam, news, txt, ur, national, team, to, , eg, england, to, , trywales, scotland, txtú, poboxoxwwq) real List(is, that, seriously, how, you, spell, his, name) real List(im, going, to, try, for, , months, ha, ha, only, joking) real List(so, ü, pay, first, lar, then, when, is, da, stock, comin) real List(aft, i, finish, my, lunch, then, i, go, str, down, lor, ard, , smth, lor, u, finish, ur, lunch, already) real List(ffffffffff, alright, no, way, i, can, meet, up, with, you, sooner) real List(just, forced, myself, to, eat, a, slice, im, really, not, hungry, tho, this, sucks, mark, is, getting, worried, he, knows, im, sick, when, i, turn, down, pizza, lol) real List(lol, your, always, so, convincing) real List(did, you, catch, the, bus, , are, you, frying, an, egg, , did, you, make, a, tea, are, you, eating, your, moms, left, over, dinner, , do, you, feel, my, love) real List(im, back, amp, were, packing, the, car, now, ill, let, you, know, if, theres, room) real List(ahhh, work, i, vaguely, remember, that, what, does, it, feel, like, lol) real List(wait, thats, still, not, all, that, clear, were, you, not, sure, about, me, being, sarcastic, or, that, thats, why, x, doesnt, want, to, live, with, us) real List(yeah, he, got, in, at, , and, was, v, apologetic, n, had, fallen, out, and, she, was, actin, like, spoilt, child, and, he, got, caught, up, in, that, till, , but, we, wont, go, there, not, doing, too, badly, cheers, you) real List(k, tell, me, anything, about, you) real Lis

In [0]:

#removing stopwords
stopWordRemover = StopWordsRemover(inputCol='MessageToken' , outputCol='Message')
textNoStopWords = stopWordRemover.transform(descTokenDF).select('Category' , 'Message')
display(textNoStopWords)


Category Message real List(go, jurong, point, crazy, available, bugis, n, great, world, la, e, buffet, cine, got, amore, wat) real List(ok, lar, joking, wif, u, oni) spam List(free, entry, , wkly, comp, win, fa, cup, final, tkts, st, may, , text, fa, , receive, entry, questionstd, txt, ratetcs, apply, overs) real List(u, dun, say, early, hor, u, c, already, say) real List(nah, dont, think, goes, usf, lives, around, though) spam List(freemsg, hey, darling, , weeks, word, back, id, like, fun, still, tb, ok, xxx, std, chgs, send, £, rcv) real List(even, brother, like, speak, treat, like, aids, patent) real List(per, request, melle, melle, oru, minnaminunginte, nurungu, vettam, set, callertune, callers, press, , copy, friends, callertune) spam List(winner, valued, network, customer, selected, receivea, £, prize, reward, claim, call, , claim, code, kl, valid, , hours) spam List(mobile, , months, u, r, entitled, update, latest, colour, mobiles, camera, free, call, mobile, update, co, free) real List(im, gonna, home, soon, dont, want, talk, stuff, anymore, tonight, k, ive, cried, enough, today) spam List(six, chances, win, cash, , , pounds, txt, csh, send, , cost, pday, days, , tsandcs, apply, reply, hl, , info) spam List(urgent, won, , week, free, membership, £, prize, jackpot, txt, word, claim, , tc, wwwdbuknet, lccltd, pobox, ldnwarw) real List(ive, searching, right, words, thank, breather, promise, wont, take, help, granted, fulfil, promise, wonderful, blessing, times) real List(date, sunday) spam List(xxxmobilemovieclub, use, credit, click, wap, link, next, txt, message, click, httpwap, xxxmobilemovieclubcomnqjkgighjjgcbl) real List(oh, kim, watching) real List(eh, u, remember, , spell, name, yes, v, naughty, make, v, wet) real List(fine, thats, way, u, feel, thats, way, gota, b) spam List(england, v, macedonia, , dont, miss, goalsteam, news, txt, ur, national, team, , eg, england, , trywales, scotland, txtú, poboxoxwwq) real List(seriously, spell, name) real List(im, going, try, , months, ha, ha, joking) real List(ü, pay, first, lar, da, stock, comin) real List(aft, finish, lunch, go, str, lor, ard, , smth, lor, u, finish, ur, lunch, already) real List(ffffffffff, alright, way, meet, sooner) real List(forced, eat, slice, im, really, hungry, tho, sucks, mark, getting, worried, knows, im, sick, turn, pizza, lol) real List(lol, always, convincing) real List(catch, bus, , frying, egg, , make, tea, eating, moms, left, dinner, , feel, love) real List(im, back, amp, packing, car, ill, let, know, theres, room) real List(ahhh, work, vaguely, remember, feel, like, lol) real List(wait, thats, still, clear, sure, sarcastic, thats, x, doesnt, want, live, us) real List(yeah, got, , v, apologetic, n, fallen, actin, like, spoilt, child, got, caught, till, , wont, go, badly, cheers) real List(k, tell, anything) real List(fear, fainting, housework, quick, cuppa) spam List(thanks, subscription, ringtone, uk, mobile, charged, £month, please, confirm, replying, yes, reply, charged) real List(yup, ok, go, home, look, timings, msg, ü, xuhui, going, learn, nd, may, lesson) real List(oops, ill, let, know, roommates, done) real List(see, letter, b, car) real List(anything, lor, u, decide) real List(hello, hows, saturday, go, texting, see, youd, decided, anything, tomo, im, trying, invite, anything) real List(pls, go, ahead, watts, wanted, sure, great, weekend, abiola) real List(forget, tell, , want, , need, crave, , , love, sweet, arabian, steed, , mmmmmm, , yummy) spam List(, , rodger, burns, , msg, , tried, call, re, reply, sms, free, nokia, mobile, , free, camcorder, please, call, , delivery, tomorrow) real List(seeing) real List(great, hope, like, man, well, endowed, , ltgt, , inches) real List(callsmessagesmissed, calls) real List(didnt, get, hep, b, immunisation, nigeria) real List(fair, enough, anything, going) real List(yeah, hopefully, tyler, cant, maybe, ask, around, bit) real List(u, dont, know, stubborn, didnt, even, want, go, hospital, ke

In [0]:
# Only keeping words with length > 2.

cleanDescriptionUdf = udf(lambda row: [x for x in row if len(x) > 2], ArrayType(StringType()))
cleanDescData = textNoStopWords.select('Category' , cleanDescriptionUdf(col('Message')).alias('Message') )

preparedData = cleanDescData.filter(size(col("Message")) > 2)

display(preparedData)

Category Message real List(jurong, point, crazy, available, bugis, great, world, buffet, cine, got, amore, wat) real List(lar, joking, wif, oni) spam List(free, entry, wkly, comp, win, cup, final, tkts, may, text, receive, entry, questionstd, txt, ratetcs, apply, overs) real List(dun, say, early, hor, already, say) real List(nah, dont, think, goes, usf, lives, around, though) spam List(freemsg, hey, darling, weeks, word, back, like, fun, still, xxx, std, chgs, send, rcv) real List(even, brother, like, speak, treat, like, aids, patent) real List(per, request, melle, melle, oru, minnaminunginte, nurungu, vettam, set, callertune, callers, press, copy, friends, callertune) spam List(winner, valued, network, customer, selected, receivea, prize, reward, claim, call, claim, code, valid, hours) spam List(mobile, months, entitled, update, latest, colour, mobiles, camera, free, call, mobile, update, free) real List(gonna, home, soon, dont, want, talk, stuff, anymore, tonight, ive, cried, enough, today) spam List(six, chances, win, cash, pounds, txt, csh, send, cost, pday, days, tsandcs, apply, reply, info) spam List(urgent, won, week, free, membership, prize, jackpot, txt, word, claim, wwwdbuknet, lccltd, pobox, ldnwarw) real List(ive, searching, right, words, thank, breather, promise, wont, take, help, granted, fulfil, promise, wonderful, blessing, times) spam List(xxxmobilemovieclub, use, credit, click, wap, link, next, txt, message, click, httpwap, xxxmobilemovieclubcomnqjkgighjjgcbl) real List(remember, spell, name, yes, naughty, make, wet) real List(fine, thats, way, feel, thats, way, gota) spam List(england, macedonia, dont, miss, goalsteam, news, txt, national, team, england, trywales, scotland, txtú, poboxoxwwq) real List(seriously, spell, name) real List(going, try, months, joking) real List(pay, first, lar, stock, comin) real List(aft, finish, lunch, str, lor, ard, smth, lor, finish, lunch, already) real List(ffffffffff, alright, way, meet, sooner) real List(forced, eat, slice, really, hungry, tho, sucks, mark, getting, worried, knows, sick, turn, pizza, lol) real List(lol, always, convincing) real List(catch, bus, frying, egg, make, tea, eating, moms, left, dinner, feel, love) real List(back, amp, packing, car, ill, let, know, theres, room) real List(ahhh, work, vaguely, remember, feel, like, lol) real List(wait, thats, still, clear, sure, sarcastic, thats, doesnt, want, live) real List(yeah, got, apologetic, fallen, actin, like, spoilt, child, got, caught, till, wont, badly, cheers) real List(fear, fainting, housework, quick, cuppa) spam List(thanks, subscription, ringtone, mobile, charged, £month, please, confirm, replying, yes, reply, charged) real List(yup, home, look, timings, msg, xuhui, going, learn, may, lesson) real List(oops, ill, let, know, roommates, done) real List(see, letter, car) real List(anything, lor, decide) real List(hello, hows, saturday, texting, see, youd, decided, anything, tomo, trying, invite, anything) real List(pls, ahead, watts, wanted, sure, great, weekend, abiola) real List(forget, tell, want, need, crave, love, sweet, arabian, steed, mmmmmm, yummy) spam List(rodger, burns, msg, tried, call, reply, sms, free, nokia, mobile, free, camcorder, please, call, delivery, tomorrow) real List(great, hope, like, man, well, endowed, ltgt, inches) real List(didnt, get, hep, immunisation, nigeria) real List(fair, enough, anything, going) real List(yeah, hopefully, tyler, cant, maybe, ask, around, bit) real List(dont, know, stubborn, didnt, even, want, hospital, kept, telling, mark, weak, sucker, hospitals, weak, suckers) real List(thinked, first, time, saw, class) real List(gram, usually, runs, like, ltgt, half, eighth, smarter, though, gets, almost, whole, second, gram, ltgt) real List(fyi, ride, early, tomorrow, morning, hes, crashing, place, tonight) real List(wow, never, realized, embarassed, accomodations, thought, liked, since, best, always, seemed, happy, cave, sorry, didnt, dont, give, sorry, offe

In [0]:
# splitting the dataset into training data and test data

train, test = preparedData.randomSplit([0.8, 0.2])
display(train)

Category Message real List(aah, bless, hows, arm) real List(aah, cuddle, lush, need, lots, tea, soup, kind, fumbling) real List(abeg, make, profit, start, using, get, sponsors, next, event) real List(abt, making, pics, bigger) real List(accidentally, brought, home, box) real List(accidentally, deleted, message, resend, please) real List(account, refilled, successfully, inr, ltdecimalgt, keralacircle, prepaid, account, balance, ltdecimalgt, transaction, ltgt) real List(actor, work, work, evening, sleep, late, since, unemployed, moment, always, sleep, late, youre, unemployed, every, day, saturday) real List(actual, exam, harder, nbme) real List(actually, decided, hungry, havent, left, yet) real List(actually, deleted, old, websitenow, blogging, magicalsongsblogspotcom) real List(actually, fuck, whatever, find, excuse, tampa, point, january, though) real List(actually, getting, ready, leave, house) real List(actually, guys, meet, sunoco, howard, right, way) real List(actually, nvm, got, hella, cash, still, ltgt, ish) real List(actually, send, reminder, today, wonderful, weekend) real List(actually, sleeping, still, might, call, back, text, rock, sis, send, text, wen, wake) real List(add, dont, really, care, cant, least, get, dude, fuck, hey, money, want) real List(addie, amp, art, ill, get, home) real List(address, test, considering, computer, isnt, minecraft, server) real List(admin, building, might, slightly, earlier, ill, call, reaching) real List(affidavit, says, ltgt, twiggs, division, courtroom, ltgt, lttimegt, ill, double, check, text, tomorrow) real List(aft, finish, lunch, str, lor, ard, smth, lor, finish, lunch, already) real List(ages, hows, abj) real List(agree, stop, thinkin, ipad, please, ask, macho, question) real List(ahhh, work, vaguely, remember, feel, like, lol) real List(ahhhhjust, woken, uphad, bad, dream, thoso, dont, like, right, didnt, know, anything, comedy, night, guess) real List(aight, call, youre, close) real List(aight, chillin, friends, room, text, youre, way) real List(aight, dats, straight, dogg) real List(aight, fuck, ill, get, later) real List(aight, ill, ask, roommates) real List(aight, ill, get, couple, minutes) real List(aight, ill, grab, something, eat, text, youre, back) real List(aight, ill, hit, get, cash) real List(aight, ill, text, back) real List(aight, ive, set, free, think, text, blakes, address, occurs, quite, sure, thought) real List(aight, latest, probably, closer, jay, tyler, two, trips) real List(aight, lemme, know, whats) real List(aight, let, know, youre, gonna, around, usf) real List(aight, plan, come, later, tonight) real List(aight, rush, ill, ask, jay) real List(aight, see, bit) real List(aight, sounds, real, want, come) real List(aight, text, address) real List(aight, text, tonight, well, see, whats) real List(aight, text, youre, back, ill, swing, need, somebody, get, door) real List(aight, thanks, comin) real List(aight, thatll, work, thanks) real List(aight, time, want, come) real List(aight, tomorrow, around, ltgt) real List(aight, well, head) real List(aight, well, keep, informed) real List(aint, answerin, phone, actually, pretty, reasonable, hour, sleepy) real List(aiya, discuss, later, lar, pick) real List(aiyah, sorry, lor, watch, watch, forgot, check, phone) real List(aiyah, wait, lor, entertain, hee) real List(aiyah, wat, long, got, improve, already, wat) real List(aiyar, dun, disturb, liao, thk, lots, aft, cupboard, come) real List(aiyar, hard, type, later, free, tell, call, scold, tell) real List(aiyo, always, one, dunno, abt, mei, haven, reply, first, time, reply, fast, lucky, workin, huh, got, bao, sugardad, ahgee) real List(aiyo, bit, pai, seh, noe, scared, dun, rem, die, hee, become, better, lookin, oredi, leh) real List(aiyo, cos, sms, neva, reply, wait, reply, lar, tot, havent, finish, lab, wat) real List(aiyo, lesson, early, still, sleepin, haha, okie, home, liao, den, confirm, lor) real List(aiyo, please, got, time, meh) real List(aiyo, poor, thing, dun

In [0]:
# counting the no. of words in training dataset
trainDataWordCount = train.count()
trainDataWordCount

Out[199]: 3945

In [0]:
# calculating classifier probability 
classProbabilities = train.groupBy('Category').count().rdd.mapValues(lambda x: (x, x / trainDataWordCount)).collectAsMap()
classProbabilities

Out[200]: {'spam': (585, 0.1482889733840304), 'real': (3360, 0.8517110266159695)}

In [0]:
#calculating unique words 
wordsFeature = train.select('Message').rdd.flatMap(lambda x: x).map(lambda x: x[0]).distinct().count()
wordsFeature

Out[201]: 1348

In [0]:
# word count in each class
trainDataWords = train.rdd.flatMapValues(lambda x: x).map(lambda x: ((x[0], x[1]), 1)).reduceByKey(lambda x,y : x+y).collectAsMap()

In [0]:
# no. of distinct classifier
distinctClass = train.rdd.map(lambda x: x['Category']).distinct().collect()
distinctClass

Out[203]: ['real', 'spam']

In [0]:
# computing probability 

def computeProbabilities(words):
    condProb = {}
    for k in distinctClass:
        condProb[k] = math.log(classProbabilities[k][1])
        classfiers = classProbabilities[k][0]
        for w in words:
            wordCount = trainDataWords.get((k, w), 0)
            probScore = (wordCount + 1) / float(classfiers + wordsFeature)
            
            likelihood = math.log(probScore)
            condProb[k] += likelihood
    return max(condProb, key=condProb.get)



In [0]:
prediction = test.rdd.map(lambda x: computeProbabilities(x['Message'])).collect()


In [0]:
accurate = test.rdd.map(lambda x: x['Category']).collect()


In [0]:
print(f"Model Accuracy: {100 * accuracy_score(prediction, accurate)} %")


Model Accuracy: 96.55172413793103 %


In [0]:
for c, (wordCount, classProb) in classProbabilities.items():
  print(f"Prior probability for '{c}': {classProb}")

Prior probability for 'spam': 0.1482889733840304
Prior probability for 'real': 0.8517110266159695
